In [1]:
from tensorflow.examples.tutorials.mnist import input_data
import tensorflow as tf
import matplotlib.pyplot as plt
import numpy as np
import os

E:\Python\PY3.6\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
mnist=input_data.read_data_sets('MNIST_data/',one_hot=True)

data_dir='./MNIST_data/'

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


In [10]:
test_images=mnist.test.images[:2]
test_labels=mnist.test.labels[:2]
test_labels.shape

(2, 10)

In [25]:
'''
load 模型
保存的模型文件有：
    1、  .meta文件：记录模型的图构造
    2、  .index和.dataxxx文件，记录参数。

所以，对一个模型不同时段保存的内容，meta文件可以共用一个（反正网络相同），
然后加载不同的.index和.dataxxx文件即可

operations
tensor
collections

这三种参数的区别

'''

'''
出现了问题：
    1、当不调用tf.reset_default_graph的时候，每次运行一次上面的程序，
       pred_result的结果就会被重复一次。从最初的[2,10],变成[2,2,10],[3,2,10],[4,2,10]
    2、原因：
       2.1 new_saver对应的两个步骤将预训练模型加载进当前的Graph。
       2.2 第一次调用，没有问题，得到正确结果。
       2.3 第二次调用，在同一个Graph上，重复加载模型，那么相当于存在两个重复的模型。
       2.4 那么，存在重复的名为'predict'的collection，运行sess.run时，是执行了两个predict
       2.5 所以第二次的结果的shape才是[2,2,10]，同理，第三次才是[3,2,10]

'''
tf.reset_default_graph()

model_dir='./Day2_Saved_Model/'
with tf.Session() as sess:
    print(sess.graph.unique_name)
    
    new_saver = tf.train.import_meta_graph(os.path.join(model_dir,'my_easy_cnn_0.96-400.meta'))
    new_saver.restore(sess,tf.train.latest_checkpoint(model_dir))
    
    # 拿到此时的graph
    graph = tf.get_default_graph()
    
    print(graph.unique_name)
    
    # 根据名称拿到input 和 ooutput
    restore_input = graph.get_tensor_by_name('x_input:0')
    restore_keep_prob = graph.get_tensor_by_name('keep_prob:0')
    restore_output = graph.get_collection('predict')
    
    pred_result = sess.run(restore_output,feed_dict={restore_input:test_images,
                                                     restore_keep_prob:1.0})
    pred_result=np.squeeze(pred_result)
    print(pred_result)
    print(len(pred_result),test_labels.shape)
    temp_acc=tf.equal(tf.argmax(pred_result,1),tf.argmax(test_labels,1))
    accuracy=tf.reduce_mean(tf.cast(temp_acc,'float'))
    print(sess.run(accuracy))
    


<bound method Graph.unique_name of <tensorflow.python.framework.ops.Graph object at 0x00000000163490B8>>
INFO:tensorflow:Restoring parameters from ./Day2_Saved_Model/my_easy_cnn_0.96-400
<bound method Graph.unique_name of <tensorflow.python.framework.ops.Graph object at 0x00000000163490B8>>
[[1.2822046e-05 1.2801580e-05 5.9274998e-06 1.0703708e-04 5.1422398e-06
  6.8234767e-05 1.2786012e-07 9.9962687e-01 3.8585971e-05 1.2238996e-04]
 [1.4158202e-02 5.9154531e-04 9.7463328e-01 7.1001081e-03 1.2195068e-05
  7.5873465e-04 2.2351402e-03 1.5766825e-06 5.0831324e-04 9.1256078e-07]]
2 (2, 10)
1.0
